Pakete laden

In [1]:
import pandas as pd
from tqdm import tqdm # Fortschrittsanzeige für pandas
tqdm.pandas()
import folium
from folium import plugins as fpg

Daten laden

In [2]:
tweet_csv = '../data/copbird_table_tweet.csv'
entity_csv =  '../data/copbird_table_entity.csv'
user_csv = '../data/copbird_table_user.csv'
cop_geolocations_csv = '../geolocations/polizei_accounts_geo.csv'

In [3]:
limit = None
tweets = pd.read_csv(tweet_csv, nrows=limit)
entities = pd.read_csv(entity_csv, nrows=limit)
users = pd.read_csv(user_csv, nrows=limit)
geolocs = pd.read_csv(cop_geolocations_csv, sep=r'\t', engine='python', nrows=limit)
# skip first two rows since they do not contain GPS data
geolocs = geolocs.iloc[2:, :]

Map für Deutschland initialisieren

In [4]:
map_ = folium.Map(location=[51.423, 9.03], zoom_start=6)

Kombination von Tweets mit GPS-Stempel

In [5]:
# Füge den Accounts, zu denen es ein GPS-Datum gibt, dieses hinzu:
users['handle'] = users['handle'].str.lower().str.strip()
geolocs['Polizei Account'] = geolocs['Polizei Account'].str.lower().str.strip()
users_geolocs = users.merge(geolocs, left_on='handle', right_on='Polizei Account', how='inner')

# Die Spalte mit dem Handle brauchen wir nur einmal:
users_geolocs.drop(columns='Polizei Account', inplace=True)
# Füge dazu, falls vorhanden, Tweets hinzu:
us_ge_tw = users_geolocs.merge(tweets, left_on='id', right_on='user_id', how='inner')
# Wieder redundante Spalte wegschmeißen:
us_ge_tw.drop(columns='id_x', inplace=True)
us_ge_tw.rename(columns={'id_y':'id'}, inplace=True)
#us_ge_tw.head()

#bad_users = users_geolocs_left.where(users_geolocs_left['LAT'].isnull()).dropna(how='all')[['id','name','handle']]
#second_try = bad_users.merge(geolocs, left_on='handle', right_on='Polizei Account', how='right')
#second_try#.where(second_try['id'].isnull()).dropna(how='all')



In [6]:
metric = 'like_count'
grouped = us_ge_tw.groupby(['LAT','LONG'])

max_counts = []
number_of_groups = grouped.ngroups
print(number_of_groups)
print(len(geolocs))
max_all = us_ge_tw[metric].max()

for i in range(0,127): #TODO rausfinden was mit der range nicht stimmt (eig. sollte number_of_groups verwendet werden)
    gps = geolocs.iloc[i][['LAT','LONG']] 
    lat = gps[0]
    long = gps[1]
    mygroup = grouped.get_group((lat, long))
    max_counts.append([lat, long, mygroup[metric].max()])
    


146
161


Experiment with the handles

In [7]:

print(users.loc[users['handle']=='polizeiberlin'])
print(geolocs.loc[geolocs['Polizei Account']=='polizeiberlin'])

            id            name         handle
57  2397974054  Polizei Berlin  polizeiberlin
   Polizei Account            Name      Typ Bundesland   Stadt        LAT  \
25   polizeiberlin  Polizei Berlin  Polizei     Berlin  Berlin  52.520007   

         LONG  
25  13.404954  


In [8]:


u = users.iloc[57]
g = geolocs.iloc[25]
#u['handle'].eq(g['Polizei Account'])
print(g)
print(u['handle'])
print(g['Polizei Account'])

Polizei Account             polizeibhv
Name               Polizei Bremerhaven
Typ                            Polizei
Bundesland                      Bremen
Stadt                      Bremerhaven
LAT                          53.539584
LONG                          8.580942
Name: 27, dtype: object
polizeiberlin
polizeibhv


In [9]:
max_likes = us_ge_tw['like_count'].max()
likes = us_ge_tw['like_count'] / max_likes
print(max_likes)

19498.0


In [10]:
locs = us_ge_tw[['LAT','LONG']]

In [11]:
#wlocs = locs.merge(pd.DataFrame(data = [likes.values] * len(locs), columns = likes.index, index=locs.index), left_index=True, right_index=True)
wlocs = pd.concat([locs, likes], axis=1)
wlocs = wlocs.dropna()
wloclist = wlocs.values.tolist()


In [12]:
folium.plugins.HeatMap(data=max_counts, radius=15, min_opacity=.5, blur=5).add_to(map_)
map_